In [1]:
import os
import os.path
from collections import Counter

In [3]:
scaffold = "/home/dzilov/pannopi_test/data/ecoli19/genome_assembly/spades/scaffolds.fasta"
blastn_taxid_out = "/home/dzilov/scripts/pgap_preparer/results/blast_results.outfmt6"
output = "/home/dzilov/prokaryotic_pipeline/dat"
scaforarg = scaffold.split("/")[-1].split(".")[0]
prefix = blastn_taxid_out.split("/")[-1].split(".")[0]

scaffolds_filtered = output + scaforarg + "_filtered.fasta"
contera_report = output + prefix + ".contera_report.txt"
vectors_log = output + prefix + ".vectors.tsv"
phages_log = output + prefix + ".phages.tsv"
adapters_report = output + prefix + ".adapters_report.outfmt6"

In [4]:
#нужно получить из бласта:
# 1) Процентное отношение бактерий в сборке (каунтер по sscinames)
# 2) Три самых часто встречающихся айди таксона (каунтер по staxids)
# 3) Части контигов, которые нужно удалить (от qstart до qend в контиге qseqid)

In [5]:
# Закинуть в правило BLAST

command = "blastn -db nt -query %s -evalue 0.000001 -outfmt '6 qseqid sseqid pident qstart qend length evalue sscinames staxids' \-num_threads 50 -out %s" % (scaffold, blastn_taxid_out)
print(command)
#os.system(command)

blastn -db nt -query /home/dzilov/prokaryotic_pipeline/data/ecoli19/unicycler/assembly.fasta -evalue 0.000001 -outfmt '6 qseqid sseqid pident qstart qend length evalue sscinames staxids' \-num_threads 50 -out /home/dzilov/prokaryotic_pipeline/data/ecoli19/blast/unicycler/Ecolli19-2_S2_L001.blast_report.tsv


In [6]:
bact_taxid = {}

vectors = []
phages = []

bact_length = Counter()
taxid_length = Counter()
total_length = 0

cont_in_nodes = {}

bact_seq = {}
with open(blastn_taxid_out) as fh:
    for line in fh:
        line = line.strip().split("\t")
        #Column names
        contig = line[0]
        ident = float(line[2])
        start = line[3]
        end = line[4]
        length = int(line[5])
        bact_full_name = line[7]
        bacteria = " ".join(line[7].split(" ")[:2])
        taxid = line[8]
        
        if "vector" in bact_full_name or "Vector" in bact_full_name:
            vectors.append(line)
        if "phage" in bact_full_name or "Phage" in bact_full_name:
            phages.append(line)
        
        bact_length[bacteria] += length
        taxid_length[taxid] += length
        total_length += length
        
        bact_seq[bacteria] = contig + ":" + start + ".." + end

In [7]:
vectors

[['66',
  'gi|1160421065|gb|KX931445.1|',
  '92.069',
  '1962',
  '5079',
  '3152',
  '0.0',
  'Suicide vector pTS1',
  '1968804'],
 ['66',
  'gi|1160421065|gb|KX931445.1|',
  '92.568',
  '1512',
  '1658',
  '148',
  '3.94e-49',
  'Suicide vector pTS1',
  '1968804'],
 ['66',
  'gi|1160421056|gb|KX931444.1|',
  '92.069',
  '1962',
  '5079',
  '3152',
  '0.0',
  'Suicide vector pME3087',
  '1968803'],
 ['66',
  'gi|1160421056|gb|KX931444.1|',
  '92.568',
  '1512',
  '1658',
  '148',
  '3.94e-49',
  'Suicide vector pME3087',
  '1968803'],
 ['66',
  'gi|984658888|dbj|LC121524.1|',
  '91.934',
  '1962',
  '5079',
  '3149',
  '0.0',
  'Cloning vector pNTR-SD',
  '1789747'],
 ['66',
  'gi|984658888|dbj|LC121524.1|',
  '91.216',
  '1512',
  '1658',
  '148',
  '8.53e-46',
  'Cloning vector pNTR-SD',
  '1789747'],
 ['66',
  'gi|40456274|gb|AY423864.1|',
  '91.544',
  '2322',
  '5079',
  '2791',
  '0.0',
  'Cloning vector pMK2016',
  '259259'],
 ['66',
  'gi|209225|gb|K03114.1|SYNPVH51CG',
  '91.

In [12]:
target_bact_seq = {}
bact_perc = Counter()
for bact, length in bact_length.most_common():
    bact_perc[bact] = length/total_length * 100
    

#             tax_id = 1
#             #length
#         elif bacteria != "Escherichia coli":
#             print(line)
# print(taxid_length)
    
print("Bacterial content is:", bact_perc.most_common(5))
print("Most common taxon ID is:", taxid_length.most_common(50))

Bacterial content is: [('Escherichia coli', 96.35693952808312), ('Shigella flexneri', 0.7367143550489041), ('Shigella sonnei', 0.6599184990534025), ('Shigella dysenteriae', 0.5614276448506137), ('Klebsiella pneumoniae', 0.4556631121054104)]
Most common taxon ID is: [('562', 1970793264), ('83334', 76777206), ('1045010', 29229479), ('2605619', 15719297), ('624', 15434652), ('622', 13053014), ('83333', 11605358), ('623', 11163460), ('573', 10279442), ('1038927', 10179548), ('155864', 9362658), ('511145', 8874514), ('1078034', 8578898), ('621', 8458516), ('216592', 6316471), ('1078021', 6017219), ('1446701', 5083383), ('566546', 4808090), ('991915', 4269859), ('595495', 4095251), ('2592065', 4062462), ('585055', 4050492), ('585056', 4024744), ('1072459', 3955184), ('386585', 3796963), ('444450', 3751409), ('316435', 3734725), ('544404', 3713290), ('1328859', 3707159), ('1048689', 3700424), ('168807', 3675859), ('701177', 3670277), ('439855', 3623147), ('1330457', 3613761), ('741093', 34563

In [48]:
print(bact_length.most_common())

[('Escherichia coli', 2431908117), ('Shigella flexneri', 18593592), ('Shigella sonnei', 16655377), ('Shigella dysenteriae', 14169612), ('Klebsiella pneumoniae', 11500270), ('Shigella boydii', 9607225), ('Salmonella enterica', 6874320), ('Yersinia pestis', 3805361), ('Escherichia albertii', 1719626), ('synthetic Escherichia', 793520), ('Escherichia fergusonii', 787619), ('Escherichia coli;Escherichia', 736406), ('Citrobacter freundii', 667973), ('Enterobacter hormaechei', 452464), ('Shigella sp.', 361203), ('uncultured bacterium', 322314), ('Enterobacter cloacae', 304382), ('Acinetobacter baumannii', 302933), ('Klebsiella quasipneumoniae', 242524), ('Proteus mirabilis', 235174), ('Klebsiella aerogenes', 226688), ('Klebsiella variicola', 181499), ('Escherichia phage', 169111), ('Salmonella sp.', 165509), ('Escherichia sp.', 154514), ('Stx2-converting phage', 151344), ('Citrobacter sp.', 142334), ('Yersinia pseudotuberculosis', 132700), ('Yersinia enterocolitica', 112466), ('Enterobacteri

In [20]:
taxid_list = []
for i in taxid_length.most_common(50):
    taxid = int(i[0])
    taxid_list.append(taxid)
print(taxid_list[:10])

[562, 83334, 1045010, 2605619, 624, 622, 83333, 623, 573, 1038927]


blastn -db nt -query /home/dzilov/prokaryotic_pipeline/data/ecoli19/unicycler/assembly.fasta -evalue 0.000001 -outfmt '6 qseqid sseqid pident qstart qend length evalue sscinames staxids' -num_threads 50 -out /home/dzilov/prokaryotic_pipeline/data/ecoli19/blast/unicycler/Ecolli19-2_S2_L001.blast_report.tsv


In [1]:
#
#
#
#
#
#
#

In [17]:
bact_report = []
for taxon, size in count_names.most_common(100):
    bact_report.append(taxon + " " + "%s%%" % round(100.*size/total_length, 2))
print("\n", bact_report, "\n")


 [] 



In [25]:
bacteria_id = []
for i in count_id.most_common()[:3]:
    bacteria_id.append(str(i[0]) + " = " + str(i[1]/total_length * 100) + "%")
print("THE MOST COMMON ID IS : " + ", ".join(bacteria_id))

THE MOST COMMON ID IS : 


In [26]:
from collections import Counter
count_names = Counter()
count_id = Counter()
total_length = 0
not_bacteria_node = []
unnown_id = []
with open(contera_log, "w") as fw:
    fw.write("UNNOWN ID'S: \n")
    for key, value in cont_to_blast.items():
        length = cont_to_len[key]
        val_split = value.split('.')[0]
        taxon_id = refids.find_one({"accession":val_split})
        print(taxon_id)
        if taxon_id == None:
            fw.write(key + " : " + val_split + "\n")
        else:
            taxon_id = taxon_id["taxid"]
            taxon_name = taxids.find_one({"_id":taxon_id})["name"]
            taxon_name = " ".join(taxon_name.split()[:2])
            count_names[taxon_name] += length
            count_id[taxon_id] += length
            total_length += length
            if taxon_name != count_names.most_common()[0][0]:
                not_bacteria_node.append(key)
                
print(not_bacteria_node)

None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None
None


In [10]:
bact_taxid = {}
with open(blastn_taxid_out) as fh:
    for line in fh:
        line = line.strip().split("\t")
        bacteria = " ".join(line[7].split(" ")[:2])
        if bacteria != "Escherichia coli":
            print(line)

['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '78528', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '72982', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '47437', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '41877', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '31272', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['1', 'gi|1707092254|gb|CP041620.1|', '0.0', '29595', '

['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '82031', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '55502', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '39709', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '32723', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '30768', '1707092254', 'CP041620', '623', 'Shigella flexneri', 'Shigella flexneri', 'Shigella flexneri strain C32 chromosome, complete genome']
['7', 'gi|1707092254|gb|CP041620.1|', '0.0', '17898', '

['10', 'gi|1347826641|gb|CP026875.1|', '1.45e-99', '383', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '1.50e-74', '300', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '1.22e-40', '187', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '1.23e-35', '171', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '4.45e-30', '152', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella boydii', 'Shigella boydii strain NCTC 9734 chromosome']
['10', 'gi|1347826641|gb|CP026875.1|', '9.91e-07', '75.0', '1347826641', 'CP026875', '621', 'Shigella boydii', 'Shigella

['14', 'gi|1002749888|gb|CP012137.1|', '1.33e-14', '100', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '4.80e-14', '99.0', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '8.02e-12', '91.6', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '8.02e-12', '91.6', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP012137.1|', '2.89e-11', '89.8', '1002749888', 'CP012137', '42897', 'Shigella flexneri 2a', 'Shigella flexneri 2a', 'Shigella flexneri 2a strain 981, complete genome']
['14', 'gi|1002749888|gb|CP0121

['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain AR-0422 chromosome']
['19', 'gi|1752751047|gb|CP044191.1|', '0.018', '60.2', '1752751047', 'CP044191', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella son

...

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP014099', '624', 'Shigella sonnei', 'Shigella sonnei', 'Shigella sonnei strain FDAARGOS_90, complete genome']
['70', 'gi|1348323427|gb|CP014099.2|', '7.05e-31', '150', '1348323427', 'CP01409

['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '2231', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '2170', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '1206', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '0.0', '1053', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete genome']
['70', 'gi|1347826600|gb|CP026784.1|', '6.43e-96', '366', '1347826600', 'CP026784', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 80-547 chromosome, complete 

['77', 'gi|1347826594|gb|CP026780.1|', '5.74e-90', '346', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '7.42e-89', '342', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '7.42e-89', '342', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '4.66e-56', '233', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 chromosome, complete genome']
['77', 'gi|1347826594|gb|CP026780.1|', '6.25e-30', '147', '1347826594', 'CP026780', '622', 'Shigella dysenteriae', 'Shigella dysenteriae', 'Shigella dysenteriae strain 53-3937 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
from collections import Counter
count_names = Counter()
count_id = Counter()
total_length = 0
not_bacteria_node = []
unnown_id = []
with open(contera_log, "w") as fw:
    fw.write("UNNOWN ID'S: \n")
    for key, value in cont_to_blast.items():
        length = cont_to_len[key]
        val_split = value.split('.')[0]
        taxon_id = refids.find_one({"accession":val_split})
        print(taxon_id)
        if taxon_id == None:
            fw.write(key + " : " + val_split + "\n")
        else:
            taxon_id = taxon_id["taxid"]
            taxon_name = taxids.find_one({"_id":taxon_id})["name"]
            taxon_name = " ".join(taxon_name.split()[:2])
            count_names[taxon_name] += length
            count_id[taxon_id] += length
            total_length += length
            if taxon_name != count_names.most_common()[0][0]:
                not_bacteria_node.append(key)
                
print(not_bacteria_node)